In [ ]:
#######################################################################
## Job: 
# Datasource : Customer Data from Snowflake Production
# Author     : 
# Target     : Snowflake GENERAL_USE_STG schema. CCF_DS_CUST_DUPLICATES
########################################################################

# Import Libraries
import numpy as np
import pandas as pd
import os
import datetime
import time
from pyspark.sql.functions import *
from pyspark.sql.types import *
from pyspark.sql.functions import from_unixtime, unix_timestamp, regexp_replace

In [ ]:
out_options = dict(sfUrl="https://ccbf.east-us-2.azure.snowflakecomputing.com",
               sfUser="SVC_P_TOOL",
               sfPassword=dbutils.secrets.get(scope = "ccbfreporting", key = "snowsvcprod"),
               sfWarehouse="CCBF_WH",
               sfDatabase="DB_BI_P_EDW",
               sfSchema="GENERAL_USE_BAS")

In [ ]:
custdata = spark.read \
  .format("snowflake") \
  .options(**out_options) \
  .option("query", """
                  SELECT
                    cust.customer_id,
                    cust.name1,
                    cust.NAME2,
                    cust.CITY,
                    cust.POSTAL_CODE,
                    cust.REGION,
                    cust.STREET,
                    cust.NAME3,
                    cust.NAME4,
                    cust.BUSINESS_TYPE,
                    cust.BUSINESS_TYPE_EXT,
                    cust.CONSUMER_TRADE_CHAN,
                    cust.CUSTOMER_SUBTRD_CHAN,
                    cust.SUPPRESSION_REASON,
                    cust.ON_BOARDING_DATE,
                    cust.PRIMARY_GROUP,
                    cust.SECONDARY_GROUP,
                    cust.ACN_NUMBER,
                    cust.SALES_ORGANIZATION,
                    cust.DISTRIBUTION_CHANNEL_ID,
                    cust.DIVISION,
                    cust.DELIVERING_PLANT,
                    cust.SALES_OFFICE,
                    cust.PREFERRED_ORDERING_METHOD,
                    cust.AUTH_MATERIAL_LIST_ID,
                    cust.LONGITUDE,
                    cust.LATITUDE, 
                    cust.CENTRAL_DELETION_FLAG
                  FROM
                    DB_BI_P_EDW.GENERAL_USE_BAS.BAS_MDM_CUSTOMER_SALES_ORG cust;
""") \
  .load()


In [ ]:
# display (custdata)

CUSTOMER_ID NAME1 NAME2 CITY POSTAL_CODE REGION STREET NAME3 NAME4 BUSINESS_TYPE BUSINESS_TYPE_EXT CONSUMER_TRADE_CHAN CUSTOMER_SUBTRD_CHAN SUPPRESSION_REASON ON_BOARDING_DATE PRIMARY_GROUP SECONDARY_GROUP ACN_NUMBER SALES_ORGANIZATION DISTRIBUTION_CHANNEL_ID DIVISION DELIVERING_PLANT SALES_OFFICE PREFERRED_ORDERING_METHOD AUTH_MATERIAL_LIST_ID LONGITUDE LATITUDE CENTRAL_DELETION_FLAG 0600589933 LYNN UNIVERSITY AIRPORT BOCA RATON 33431-5598 FL 3601 N MILITARY TRL IS AIRPORT MULTI 04 L 29 215 S 2013-08-08 B5922 N3952 4500 Z3 Z0 I017 I017 FSV SUPPRESS -80.121292000000 26.384051000000 X 0500339726 FLORIDA MEMORIAL UNIVERSITY MIAMI GARDENS 33054-6155 FL 15800 42ND AVE NW IS FIU CAMPUS BUILDING MULTI 04 L 29 215 S 2016-12-16 B5921 N3946 4500 Z3 Z0 I017 I017 FSV SUPPRESS -80.268325000000 25.917740000000 X 0600590139 LYNN UNIVERSITY MOHAMMED BOCA RATON 33431-5598 FL 3601 N MILITARY TRL IS 2ND FL 04 L 29 215 2014-07-16 B5922 N3952 4500 Z3 Z0 I017 I017 FSV I017 -80.121300000000 26.384970000000 0500139144 SOUTHEASTERN UNIV MI CASA LAKELAND 33801-6034 FL 1000 LONGFELLOW BLVD CCNA 01 S 99 260 S 2012-06-04 B5923 N3958 7534124 4500 Z1 Z0 I004 I004 SRVC SUPPRESS -81.919431000000 28.031589000000 X 0600863929 CROWNE PLAZA HOTEL FLL HOTELS INC FORT LAUDERDALE 33312-4812 FL 2800 W STATE ROAD 84, STE 119 01 1 2016-11-25 4500 Z1 Z0 -80.178321000000 26.085912000000 0600428473 SCHOOL BOARD OF NASSAU COUNTY FERNANDINA BEACH 32034-3403 FL 1201 ATLANTIC AVE 01 1 2016-08-24 4500 Z1 Z0 -81.455525000000 30.670375000000 0600370597 CANOE CREEK DUNKIN DONUTS SAINT CLOUD 34769 FL 229 TURNPIKE MILE MARKER 01 1 19 261 2009-06-09 A0337 A9999 4500 Z1 Z0 I001 I001 EDI LIMITED I001 -81.273476000000 28.094414000000 0600367030 THAI BASIL THAI BASIL OF ORLANDO INC WINTER SPRINGS 32708-5082 FL 5800 RED BUG LAKE RD 01 1 18 153 2006-03-29 B2992 A9999 4500 Z1 Z0 I001 I001 ECOM BROWN BOX -81.268273000000 28.648979000000 0600382932 KRISPY KREME JACKSONVILLE 32210-7733 FL 6250 103RD ST CCNA 01 S 99 260 2014-09-03 A9999 A9999 1732079 4500 Z1 Z0 I002 I002 SRVC SERVICE ONLY -81.744230000000 30.248380000000 0501435329 YORK FD SITE# 75 LARGO 33773-3742 FL 12161 62ND ST STE 3 2ND VOL ONLY X X 18 153 2022-09-22 A9999 A9999 4500 Z1 Z0 I000 I030 INCL SECONDARY VOL -82.767285000000 27.884300000000 0501504241 CCNA BEEF O BRADYS GOLF OUTING 2023 LUTZ 33558-5327 FL 4312 CHEVAL BLVD ISIS KOLLAR 01 U 262 280 2023-03-30 A0017 NCCNA 4500 Z1 Z0 I000 I000 HOUS LIMITED I000 0E-12 0E-12 0501363296 ALLORA BISTROT ALLORA INC FERNANDINA BEACH 32034 FL 11 NORTH 3RD STREET 01 1 18 153 2022-03-22 A9999 A9999 4500 Z1 Z0 I002 I002 ECOM LIMITED I002 -81.462880000000 30.671870000000 0501409630 HIP HOP SEAFOOD CHICKEN ODEH FOOD SERVICE INC DAYTONA BEACH 32114 FL 988 ORANGE AVENUE 01 1 147 15 2022-07-19 B2992 A9999 4500 Z1 Z0 I001 I010 ECOM BROWN BOX -81.037110000000 29.200335000000 0501412423 MIAMI K DISTRIBUTORS INC POMPANO BEACH 33064 FL 1301 W COPANS RD 2ND VOL ONLY X X 18 153 2022-07-25 A9999 A9999 4500 Z1 Z0 I017 I017 INCL SECONDARY VOL -80.142465000000 26.260420000000 0501328521 TURMERIC INDIAN CUISINE TURMERIC LLC SARASOTA 34236 FL 1001 COCOANUT AVENUE BARRY PATEL 01 1 18 153 2022-01-16 B2992 N1339 4500 Z1 Z0 I005 I005 ECOM BROWN BOX -82.544715000000 27.345895000000 0501361461 WILLIAM MYERS SITE# 2 WINTER HAVEN 33884-3534 FL 5357 SNEAD DR 2ND VOL ONLY X X 18 153 2022-03-16 A9999 A9999 4500 Z1 Z0 I004 I004 INCL SECONDARY VOL -81.665446000000 27.951295000000 0501389973 ORCHID COVE CLEARWATER 33765-1132 FL 1980 SUNSET POINT RD #R 2ND VOL ONLY X X 19 261 2022-06-05 A9999 A9999 4500 Z1 Z0 I000 I030 INCL SECONDARY VOL -82.756830000000 27.990005000000 0501438720 CS COUNTRY DINER 541 BEVILLE LLC OAK HILL 32759 FL 741 U.S. 1 01 1 18 153 2022-10-05 B2992 N7266 4500 Z1 Z0 I001 I010 ECOM BROWN BOX -80.843871000000 28.830643000000 0501501803 LA BRASA ROTISERIE GRILL MIAMI 33162-3505 FL 16605 NE 4TH AVE 2ND VOL ONLY X X 19 261 2023-03-23 A9999 A9999 6925745 4500 Z1 Z0 I017 I017 INCL SECONDARY VOL -80.192270000000

In [ ]:

# Custom Code for Identifying Duplicate Customers and create dataframe to write into Snowflake Table

# NOTE_1: this code is specifically for the Brevard data set and some modifications may be appropriate for data for other regions. There is a Miami example that I will discuss at the bottom
# NOTE_2: this code does not automatically import the Equipment? column and should like I did with other merges and imports here

# Applying the Algorithm: Some things to note from when I tried to replicate the code. This should fix some errors, at least the ones I encountered. I will try to touch on them in the relevant cells as well. 07/26/2023
'''Applying the Algorithm
1. Change any filenames being imported in the code to match with the desired files. Do the same with files the code creates
2. Importing any coodinate data may not be needed as it is SAP now for all sales offices
3. Got a file for all equipment for all customers, so I am going to use the code to import it itself without having to do a vlookup.
4. Code only accepts work in csv format and outputs work in csv. Desired excel files need to be saved as csv
5. Primary volume and secondary volume may not be in the data, comment part of code that tries to drop these columns to prevent errors.
6. When the code drops the customers that have the first three numbers as "899" you may need to convert the whole columns as a string first to prevent errors.
7. Customer column must be changed to "Customer ID" in the code (then change every instance of "Customer ID" to "Customer") or changed the column name in the csv to "Customer ID"
8. Make sure that the Customer numbers in the customer data file and the Customer numbers in the equipment file are both converted to strings in the code
9. To setup the volume file, you need to delete the horizontal columns on the top left and name the customer ids as "CUSTOMER_ID"
10. You may not have to drop the merged CUSTOMER_ID as the cell does before the volume_data is merged (not read). So just comment out the cell
11. Rename the line of code at top that reads the sales office data to reflect the sales office data you're working with and rename the line at the bottom that creates the final output as csv
12 All files being worked with need to be in the same folder
'''

#Along with those notes. I also am now able to merge the equipment data from a file automatically with a file that was sent to me for all customers that have equipment. Here are some useful lines of code to do that
'''
equipment = pd.read_csv("eq_check_7.24.2023.csv")       Put this where other files are being read, if you have the equipment file 
'''

'''

df['Customer'] = df['Customer'].astype(str)


equipment['PARTNER_SH'] = equipment['PARTNER_SH'].astype(str)


df["Equipment?"] = df["Customer"].isin(equipment["PARTNER_SH"]).map({True: "Y", False: "N"})       This is for when you want put Y or N for when the account has equipment according to the file we just read. The two reference columns are also converted to strings so that they may match. (123 =/= "123"). I would run this before merging any other columns, right after the other files being used are read.
'''

In [ ]:
df['Street'] = df['Street'].fillna('') # This will prevent an error that occurs because an account may not have a listed street name

# Setting up and Importing Data

In [ ]:
import pandas as pd #import pandas

In [ ]:
df = pd.read_csv("I013_brevard_customers_upd.csv") #read the file with equipment (Y/N) column from Aleks for Brevard's customer accounts. Needs code to just join them later.

In [ ]:
df.columns #display all columns

In [ ]:
#df['Customer'] = df['Customer'].astype(str) Uncomment if it is not as a string already and giving an error

df = df[~df['Customer'].str.startswith('899')] # Removes all customers whose IDs start with 899


In [ ]:
df = df[df['Preferred Ordering Method'] != 'FSV'] # Excludes customers with preffered ordering method FSV

In [ ]:
df = df.drop(['Name 3', 'Name 4','ACN Number', 'Customer Trade Chan', 'Customer Subtrd Chan', 'Sales Organization', 'Distribution Channel', 'Primary Volume', 'Secondary Volume' ], axis = 1) # This drops columns that are really needed for the analysis. NOTE: May need to exclude Primary Volume and Secondary Volume

In [ ]:
brevard_coor_data = pd.read_csv('Brevard_Customers.csv') # Reading coordinate data. If you dont have coordinates file, then comment this out

In [ ]:
volume_data = pd.read_csv('6 m volume 062023.csv') # Reading volume data from Diana (6 month) if you have it

In [ ]:
last_delivery = pd.read_csv('Customer Last Delivery Report.csv') # Reading last delivery data from Brian if you have it

In [ ]:
df = pd.merge(df, brevard_coor_data[["CUSTOMER_ID", 'LONGITUDE', 'LATITUDE']], left_on = df["Customer"], right_on='CUSTOMER_ID', how = 'left') # Adds CUSTOMER_ID, longtitude and latitude based on CUSTOMER_ID of a another file

In [ ]:
df = df.drop('CUSTOMER_ID', axis = 1) # Drops the joined CUSTOMER_ID column because we already have that information. This may give you an error, just comment it out if you don't need it

In [ ]:
df = pd.merge(df, volume_data[['CUSTOMER_ID', 'Volume', 'Secondary Volume']], left_on=df['Customer'], right_on='CUSTOMER_ID', how='left') # Adds CUSTOMER_ID, longtitude and latitude based on CUSTOMER_ID of a another file

In [ ]:
df = df.drop('CUSTOMER_ID', axis = 1) # Drops the joined CUSTOMER_ID column because we already have that information

In [ ]:

last_delivery["Customer Number"] = last_delivery["Customer Number"].astype(str)
# Converts customer number to a string in the last_delivery

In [ ]:
last_delivery["Customer Number"] = last_delivery["Customer Number"].str.rstrip('.0')
# Gets rid of any part of the customer number string in last_delivery that's '.0'

In [ ]:
df = pd.merge(df, last_delivery[['Customer Number', 'Last Delivery Date']], left_on=df['Customer'], right_on=last_delivery['Customer Number'], how='left')
# Joins last_delivery data into the main dataframe (df) based on customer number.

# Finding Similarities

In [ ]:
df['dba_marker'] = df.duplicated(subset= 'Name', keep=False) #Makes a column that returns "True" if an exact account name is found in another account

In [ ]:
df['street_marker'] = df.duplicated(subset= 'Street', keep=False) #makes a column that returns "True" if an exact account street is found in another account

In [ ]:
dbaname_duplicates= df.loc[df.dba_marker == True] # Likely not needed, but this make a dataframe with only accounts that has exact name matches

In [ ]:
street_duplicates = df.loc[df.street_marker == True] # Likely not needed, but this make a dataframe with only accounts that has exact street matches

In [ ]:
street_duplicates = street_duplicates.sort_values(by=['Street']) # Sorts by street name so you can see the duplicate streets next to each other, not needed

In [ ]:
def check_similar_streets(value, series):
    similar_streets = []
    for other_value in series:
        if value != other_value and (value in other_value or other_value in value):
            similar_streets.append(other_value)
        elif value == other_value:
            similar_streets.append(other_value)
    return similar_streets


"""
The result will be a column whose rows (account) contains a list of strings that are similar to that account's street name, and it will be done for every row.
This functiontakes an arbitrary value and a data series' column. It creates an empty list. A second value is created that becomes each entry in the column.
If an arbirary value doesn't equal that entry and if an arbitrary value's string is in the row's entry or vice versa, then add the row's value from the 
data series to the empty list. 
 
"""

In [ ]:
similar_streets_list = []
for value in df["Street"]:
    similar_streets = check_similar_streets(value, df["Street"])
    similar_streets_list.append(similar_streets)

df["similar_streets"] = similar_streets_list


"""
Here, we create an empty list to store our results from the function we created later. Remember, our function takes an arbitrary value as one of the arguments
along with the data column. So, we create that value as it iterates through the 'Street' column to get compared to other_value, another iterated value created
by the function. We store the results of the function in the empty list and then turn that list into a new column in the data frame.

"""

In [ ]:
def get_similar_streets_id(value, series, customer_series):
    similar_streets = []
    for i, other_value in enumerate(series):
        if value != other_value and (value in other_value or other_value in value):
            similar_streets.append(customer_series[i])
        elif value == other_value:
            similar_streets.append(customer_series[i])
    return similar_streets

'''
Now, we want to match the similar names we found with their Customer IDs. This function takes an arbitrary value, and two data series. The first 
series would be what we want to match the Customer IDs to, and the second series will be the Customer IDs. The function will create an empty list
and loop two arbirary values in an enumerated series. An enumerated series tells us the index and value of each row/account in a column. Then we check
if the value is similar to other values like we did in the previous function created. For only those similar values, when then only add to the empty list
the their indexes in the Customer column so that they could be matched to the ID.

'''

In [ ]:
df = df.reset_index(drop=True) # Resets the index of the rows

In [ ]:
similar_streets_id_list = []
for i, value in enumerate(df['Street']):
    similar_streets_id = get_similar_streets_id(value, df['Street'], df['Customer'])
    similar_streets_id_list.append(similar_streets_id)

df['similar_streets_id'] = similar_streets_id_list

''' 
We create an empty list to store our results in later. We create two arbitrary values, i and value, that will enumerate through the Street column. 
These two values will be assigned all the values and indexes inside that column. Then the function we created will be used as explained above and the
results will be added to our empty list to be transformed into a column in the data.

'''

In [ ]:
def check_similar_names(value, series):
    similar_names = []

    for other_value in series:
        if value != other_value and (value in other_value or other_value in value):
            similar_names.append(other_value)
        elif value == other_value:
            similar_names.append(other_value)
    return similar_names

# Does the same as the first function created but for DBA names, please see comments.

In [ ]:
similar_names_list = []
for value in df['Name']:
    similar_names = check_similar_names(value, df['Name'])
    similar_names_list.append( similar_names)

df['similar_names'] = similar_names_list

# Also similar to the step made after the creation of the first function, but with similar DBA names.

In [ ]:
def get_similar_names_id(value, series, customer_series):
    similar_names = []
    for i, other_value in enumerate(series):
        if value != other_value and (value in other_value or other_value in value):
            similar_names.append(customer_series[i])
        elif value == other_value:
            similar_names.append(customer_series[i])
    return similar_names

# Does the same as second function created but for DBA names, please see comments.

In [ ]:
similar_names_id_list = []
for i, value in enumerate(df['Name']):
    similar_names_id = get_similar_names_id(value, df['Name'], df['Customer'])
    similar_names_id_list.append(similar_names_id)

df['similar_names_id'] = similar_names_id_list

# Also similar to the step made after the creation of the second function, but with similar DBA names.

In [ ]:
combined_list = [item for sublist in df['similar_names_id'] for item in sublist] + [item for sublist in df['similar_streets_id'] for item in sublist] + [item for sublist in street_duplicates['Customer'] for item in sublist]+[item for sublist in dbaname_duplicates['Customer'] for item in sublist]


'''
This is a combination of different lists different columns. Each expression starts with an inner loop that is performed first, 'for item in sublist'. item will loop through whatever sublist is at the time. In 'for sublist df[column name], sublist is then iterated through the column and sublist becomes the values in those respect columns. As a result, the inner loop now has values stored as 'sublist' to be iterated through which will become 'item'. The leading variable in that expression, 'item', makes the expression return what is stored in 'item'.
'''

In [ ]:
unique_numbers = list(set(combined_list))

print(unique_numbers)

# The set function returns finds all the unique numbers in the combined list. The list function converts this set of numbers to a list to be
# combatible with the data series.

In [ ]:
df.loc[df['Customer'].isin(unique_numbers)].to_csv('I013_keyyed.csv', index = False)

# The rows in the data set are now filtered by Customer IDs whose string are somewhere in the list of the unique nunbers and turned into a csv file.

# Grouping the Data

In [ ]:
# df = df [~((df['similar_streets_id'].apply(lambda x: isinstance(x, list) and len(x) == 1)) | (df['similar_names_id'].apply(lambda x: isinstance(x, list) and len(x) == 1)))] # This will exclude any customer that has only one similar street ID or name ID because it would only be including itself
# result = df.head() 

In [ ]:
df['Combined'] = df.apply(lambda row: row['Street'] + ' ' + row['Name'] if any(row['Street'][:3] == street[:3] for street in df['Street'] ) else '', axis=1) # If the first three characters of a customer's street is in any other customer street, then the street and name of the customer will be added together in a 'Combined' column. In other words, based on the first three characters of a street, groups will be created if they have the same name.



In [ ]:
df['Group'] = df['Combined'].astype('category').cat.codes
df['Group'] = (df['Group'] + 1).astype(str) # This gives all the unique combinations, from the "Combined" column, of street and name combinations a group number.

In [ ]:
group_freq = df['Group'].value_counts()
df['# of Group Members'] = df['Group'].map(group_freq) # Counts the members in a group


In [ ]:
df['Subgroup']=df['Group']+ "_" + df['Name'].str[:3] # Creates a subgroup where the number is the group number and after the underscore is the first three characters of the customer name. So, if in a group, two customer names start with the same first three characters, they will be in the same subgroup.

In [ ]:
sub_group_freq = df['Subgroup'].value_counts()
df['# of Subgroup Members'] = df['Subgroup'].map(sub_group_freq) # Counts members in the subgroup


In [ ]:
df = df.drop("key_0", axis=1)
#Drops a not needed column of customer numbers that was generated by one of the merges

In [ ]:
df.reset_index(drop=True, inplace=True)
#Reset index again

In [ ]:
# df.to_csv('I013_grouped_duped_subgroups.csv', index = False)
# df.to_excel('I013_grouped_duped_subgroups.xlsx', index=False)
# # Converts work done so far to a csv and Excel file

# Conditioning the Data

In [ ]:

df.dtypes
# Displays data types of all columns

In [ ]:
df['dba_marker'] = df['dba_marker'].astype(str)
df['street_marker'] = df['street_marker'].astype(str)

# Converts dba_marker and street_marker to string from bool to work with later

In [ ]:

df.dtypes
# Displays data types of all columns to ensure above conversion

In [ ]:
import pandas as pd
df['action'] = '' # Creates an empty column called "action"



df['Suppression Reason'].fillna("", inplace=True) #if null, replaces with empty string

df['Secondary Volume'].fillna("0", inplace=True) #if null, replaces with empty string



# First, let's create a condition to check if the row satisfies all the criteria
condition_1 = (  # "if there is an active and a suppressed account and there is no equipment on the suppressed and there is no secondary volume on the suppressed then no action for both"
    (df['dba_marker'] == True) & # and we want the condition only applied to accounts that share at least one duplicated name
    (df['street_marker'] == True) &  # and we want the condition only applied to accounts that share at least one duplicated street
    (df['# of Subgroup Members'] == 2) &  # and we only want the condition applied to subgroups with 2 members
    (df['Suppression Reason'] != "") & # and no suppression check
    ((df['Secondary Volume'].isin(["", "0", "0.0"])) | (df['Equipment?'] == 'N')) #  and no equipment check or no secondary volume check
)


# Set 'action' column to 'no' for rows that satisfy condition_1
df.loc[df.groupby('Subgroup')['Subgroup'].transform(lambda x: any(condition_1.loc[x.index])), 'action'] = 'no'

condition_2 = (  # "if there is an active account and a suppressed account and the suppressed account has equipment or secondary volume it needs to be highlighted for further action to both accounts in subgroup"
    (df['dba_marker'] == True) & # and we want the condition only applied to accounts that share at least one duplicated name
    (df['street_marker'] == True) & # and we want the condition only applied to accounts that share at least one duplicated street
    (df['# of Subgroup Members'] == 2) & # and we only want the condition applied to subgroups with 2 members
    (df['Suppression Reason'] != "") & # and no suppression check
    ((~df['Secondary Volume'].isin(["", "0", "0.0"])) | (df['Equipment?'] == 'Y')) # or has secondary volume check

)
df.loc[df.groupby('Subgroup')['Subgroup'].transform(lambda x: any(condition_2.loc[x.index])), 'action'] = 'yes'
# applies "yes" in the action column for rows that meet conidtion 1 based on subgroup



condition_3 = ( # "if there is more than 1 account that is active, has equipment, or has secondary volume in a subgroup, then mark for action" 
    (df.groupby('Subgroup')['Suppression Reason'].transform(lambda x: (x == '').sum()) > 1) | # More than one active account check for accounts grouped by subgroup
    (df.groupby('Subgroup')['Equipment?'].transform(lambda x: (x == 'Y').sum()) > 1) | # More than one account has equipment check for accounts grouped by subgroup
    (df.groupby('Subgroup')['Secondary Volume'].transform(lambda x: ~(x.isin(['', '0', '0.0'])).sum()) > 1) # More than one account has secondary volume check for accounts grouped by subgroup
)

# Set 'action' column to 'duped' for rows that satisfy condition_3 within each group
df.loc[df.groupby('Subgroup')['Subgroup'].transform(lambda x: any(condition_3.loc[x.index])), 'action'] = 'duped'


In [ ]:
df.to_csv("I013_conditional.csv")
# Converts current progress to a CSV file

# The Miami Issue

In [ ]:
'''
Miami has an issue with the retrieval of similar names where it thinks that an account name with the letter "I" or the string "TUR" is similar to another account due to a DBA Name of an account that is called "I". We know that just because two account names have the letter "I", that does not mean the name is similar at all. The loop that finds the similar names and the loop that finds the similar IDs needs to have something of this nature applied to ignore problematic names when discovered. This is an example with the "I" issue:

def get_similar_names_id(value, series, customer_series):
    similar_names = []
    similar_names_id = []
    for i, other_value in enumerate(series):
        if value != other_value and other_value != "I" and (value in other_value or other_value in value):
            similar_names.append(other_value)
            similar_names_id.append(customer_series[i])
    return similar_names, similar_names_id

similar_names_id_list = []
for i, value in enumerate(df['Name - DBA Name']):
    if value != "I":
        similar_names, similar_names_id = get_similar_names_id(value, df['Name - DBA Name'], df['Customer'])
    else:
        similar_names, similar_names_id = [], []
    similar_names_id_list.append(similar_names_id)

df['similar_names_id'] = similar_names_id_list

OR

You can drop the rows that are causing the issue before running any of the loops and then reinsert them. The code above will just exclude it from the loop.
'''

Out[3]: '\nMiami has an issue with the retrieval of similar names where it thinks that an account name with the letter "I" or the string "TUR" is similar to another account. We know that just because two account names have the letter "I", that does not mean the name is similar at all. The loop that finds the similar names and the loop that finds the similar IDs needs to have something of this nature applied to ignore problematic names when discovered. This is an example with the "I" issue:\n\ndef get_similar_names_id(value, series, customer_series):\n similar_names = []\n similar_names_id = []\n for i, other_value in enumerate(series):\n if value != other_value and other_value != "I" and (value in other_value or other_value in value):\n similar_names.append(other_value)\n similar_names_id.append(customer_series[i])\n return similar_names, similar_names_id\n\nsimilar_names_id_list = []\nfor i, value in enumerate(df[\'Name - DBA Name\']):\n if value != "I":\n similar_names, similar_names_id = get_similar_names_id(value, df[\'Name - DBA Name\'], df[\'Customer\'])\n else:\n similar_names, similar_names_id = [], []\n similar_names_id_list.append(similar_names_id)\n\ndf[\'similar_names_id\'] = similar_names_id_list\n\nOR\n\n\n'